# Montenegrin Independence Referendum

Let's explore the results of the Montenegrin independence referendum in 2006.

The dataset was downloaded from Wikipedia article
["2006 Montenegrin independence referendum"](https://en.wikipedia.org/wiki/2006_Montenegrin_independence_referendum).

In [1]:
import pandas as pd

from lets_plot import *

In [2]:
LetsPlot.setup_html() 

In [3]:
def get_data(df):
    # Blank or invalid votes:
    df["Blank"] = df["Voted"] - df["Yes"] - df["No"]
    df = df[["Municipality", "Registered", "No", "Yes", "Blank"]]
    return pd.melt(df, id_vars=["Municipality", "Registered"], var_name="Vote", value_name="Number")

def get_geodata(df):
    from lets_plot.geo_data import geocode_states
    country = "Montenegro"
    municipalities_geocoder = geocode_states(names=df["Municipality"]).scope(country)
    return municipalities_geocoder, pd.merge(
        municipalities_geocoder.get_boundaries(resolution=15),
        df[["Municipality", "Yes%"]],
        left_on="state",
        right_on="Municipality"
    )

In [4]:
raw_df = pd.read_csv("https://raw.githubusercontent.com/JetBrains/lets-plot-docs/master/data/montenegrin_referendum_2006.csv")
df = get_data(raw_df)
municipalities_geocoder, boundaries_gdf = get_geodata(raw_df)

The geodata is provided by © OpenStreetMap contributors and is made available here under the Open Database License (ODbL).


In [5]:
ggplot() + \
    geom_livemap(data_size_zoomin=3) + \
    geom_map(aes(fill="Yes%"), data=boundaries_gdf,
             tooltips=layer_tooltips().title("@state")
                                      .line("'Yes' votes|@{Yes%}")
                                      .format("Yes%", "{} %")) + \
    geom_pie(aes("Municipality", paint_a="Vote", weight="Number", size="..sum..", group="Municipality"),
             data=df, map=municipalities_geocoder, map_join=["Municipality", "state"],
             fill_by='paint_a', hole=.2, stroke=1.5, stroke_side='both',
             tooltips=layer_tooltips().title("@Municipality")
                                      .line("Vote|@Vote")
                                      .line("Number|@{..count..}")
                                      .line("Percent|@{..prop..}")
                                      .line("Total voted|@{..sum..}")
                                      .line("Registered|@Registered")
                                      .format("..prop..", ".2%")
                                      .format("Registered", ",d")) + \
    scale_fill_gradientn(["#a50026", "#d73027", "#66bd63", "#4daf4a", "#006837"]) + \
    scale_manual('paint_a', values=["#e41a1c", "#4daf4a", "#999999"]) + \
    scale_size(name="Total voted", range=[3, 8]) + \
    ggtitle("Results of the Montenegrin independence referendum, 2006") + \
    ggsize(900, 900) + \
    theme(legend_position='none', plot_title=element_text(size=24, face='bold'))